#Utility and Neural Network

In [ ]:
graph = {1: {49, 2, 50}, 2: {48, 1, 3}, 3: {8, 2, 4}, 4: {3, 5}, 5: {4, 6}, 6: {10, 5, 7}, 7: {8, 12, 6}, 8: {9, 3, 7}, 9: {8, 10}, 10: {9, 11, 6}, 11: {16, 10, 12}, 12: {11, 13, 7}, 13: {12, 14}, 14: {13, 15}, 15: {16, 14}, 16: {17, 11, 15}, 17: {16, 18}, 18: {17, 19}, 19: {18, 20}, 20: {19, 21}, 21: {20, 22, 23}, 22: {27, 21, 23}, 23: {24, 21, 22}, 24: {25, 23}, 25: {24, 26}, 26: {25, 27}, 27: {26, 28, 22}, 28: {27, 29}, 29: {28, 30}, 30: {29, 31}, 31: {32, 30}, 32: {33, 31}, 33: {32, 34, 38}, 34: {33, 35, 36}, 35: {34, 36, 39}, 36: {34, 35, 37}, 37: {41, 36, 38}, 38: {33, 37, 39}, 39: {40, 35, 38}, 40: {41, 43, 39}, 41: {40, 42, 37}, 42: {41, 43, 45}, 43: {40, 42, 44}, 44: {43, 45}, 45: {42, 44, 46}, 46: {45, 47}, 47: {48, 46}, 48: {49, 2, 47}, 49: {48, 1, 50}, 50: {49, 1}}

In [30]:
import numpy as np
import random
import math

from queue import Queue 

def retraced_path(prev,curr_node,goal): #* changed prev in func def
    #print("entering retracd path") #* no need to print
    fwd_path = {}
    #fwd_stack = LifoQueue()
    cell = goal #4,4
    
    while prev[cell]!= None and cell != curr_node  :
        
        fwd_path[prev[cell]] = cell
        #fwd_stack.put((cell,prev[cell]))
        cell = prev[cell]
        
   
     #* return the path to be followed by the agent in the order from starting to end
    return len(fwd_path.keys())

    
def bfs(curr_pred_node,curr_agent_node):
    goal = curr_agent_node
    queue = Queue()
    prev = {
        curr_pred_node: None
    }
    visited = set()
    queue.put(curr_pred_node)
    #explore = []
    while queue.empty() == False:
        curr_state = queue.get()
        
        
        if curr_state not in visited:
           # explore.append(curr_state)
        
            if curr_state == goal:
                #print("found the path for agent 1") #, curr_state,prev) # #* no need to print
                #print(explore) #* no need to print
                shortest_path = retraced_path(prev,curr_pred_node,goal)
                return shortest_path
                #break
            else:
                for child in graph[curr_state]:
                    if child not in visited : 
                    
                        queue.put(child)
                        if child not in prev.keys():# --> check this
                            prev[child] = curr_state
                visited.add(curr_state)
    
    return 




def move_prey(curr_prey_node):
    prey_neighbors = [node for node in graph[curr_prey_node]]
    prey_neighbors.append(curr_prey_node)
    selected_prey_neighbor = random.choice(prey_neighbors)
    #print(selected_prey_neighbor)
    return(selected_prey_neighbor)
def move_predator(curr_pred_node,curr_agent_node,prob_req = False): #* added prob req for agent 5 to get the denominator of probability
    min_dist_to_agent = math.inf
    breaking_ties_list = []
    for neighbor in graph[curr_pred_node]:
        dist_to_agent = bfs(neighbor,curr_agent_node)
        if dist_to_agent <= min_dist_to_agent:
            min_dist_to_agent = dist_to_agent
            #selected_pred_neighbor = neighbor
            breaking_ties_list.append(neighbor)
    if prob_req == True:    #* added prob req for agent 5 to get the denominator of probability
        return breaking_ties_list
                
        #print(breaking_ties_list)
    selected_pred_neighbor = random.choice(breaking_ties_list)

    
    return(selected_pred_neighbor)

In [31]:
import random
import math
def move_distracted_predator(curr_pred_node,curr_agent_node,prob_req = False): #* added prob req for agent 5 to get the denominator of probability
    min_dist_to_agent = math.inf
    breaking_ties_list = []
    for neighbor in graph[curr_pred_node]:
        dist_to_agent = bfs(neighbor,curr_agent_node)
        if dist_to_agent <= min_dist_to_agent:
            min_dist_to_agent = dist_to_agent
            #selected_pred_neighbor = neighbor
            breaking_ties_list.append(neighbor)
    if prob_req == True:    #* added prob req for agent 5 to get the denominator of probability
        return breaking_ties_list
                
        #print(breaking_ties_list)
    pred_neighbour_close = random.choice(breaking_ties_list) #* this points to the 0.6 prob part
    #print(graph[curr_pred_node]) #* del this later
    pred_neighbour_all = random.choice(list(graph[curr_pred_node])) #* this points to the 0.4 prob part
    selected_pred_neighbor = random.choices([pred_neighbour_close,pred_neighbour_all],weights = [0.6,0.4])[0]

    
    return(selected_pred_neighbor)



In [32]:
#State Dictionary

states = {}
for agent in range(1,51):
    for prey in range(1,51):
        for pred in range(1,51):
            states[(agent,prey,pred)] = 0

In [33]:
#Action Dictionary
actions = {}
for s in states.keys():
    actions[s] = list(graph[s[0]])


In [24]:
#Utility Dictionary
def utility():
    V = {}
    for s in states.keys():
        if s[0] == s[2]:
            V[s] = 10000
        elif s[0] == s[1]:
            V[s] = 0
        elif s[2] in graph[s[0]]:
            V[s] = 10000
        elif s[1] in graph[s[0]]:
            V[s] = 0
        else:
            V[s] = 100
    return V

In [ ]:
#Reward Dictionary
rewards ={}
for s in actions.keys():
    for a in actions[s]:
        if s[2] == a:
            rewards[(s,a)] = 1000
        elif s[1] == a:
            rewards[(s,a)] = 0
        else:
            rewards[(s,a)] = 10

In [ ]:
#Transition Probabilities Dictionary
trans = {}

for row in states.keys():
    for col in states.keys():
        if col[0] in graph[row[0]]:
            if col[1] in graph[row[1]] or col[1] == row[1]:
                if col[2] in graph[row[2]]:
                    if len(graph[row[1]])==2:
                        trans[(row, col)] = 1/3
                    else:
                        trans[(row, col)] = 1/4

In [ ]:
#for pred 

for state1, state2 in trans.keys():
    blt = move_distracted_predator(state1[2],state2[0],prob_req = True) #returns all possible neighbours on thre shortest paths
    if state2[2] in blt:
        trans[(state1,state2)]*= 0.6/len(blt) + 0.4/len(graph[state1[2]]) #1/len(blt)
    else:
        trans[(state1,state2)]*=  0.4/len(graph[state1[2]])#0


In [ ]:
import pickle
import os

filename = "trans.pkl"
with open(filename, 'wb') as f:
    pickle.dump(trans,f)

In [ ]:
import pickle
filename = "trans.pkl"
if os.path.exists(filename):
    with open(filename, 'rb') as f:
        trans = pickle.load(f)

In [ ]:
ref = {}

for row in states:
    for col in states:
        if col[0] in graph[row[0]]:
            if col[1] in graph[row[1]] or col[1] == row[1]:
                if col[2] in graph[row[2]]:
                    if row in ref.keys():
                        ref[row].append(col)
                    else:
                        ref[row] = [col]

In [19]:
import pickle
filename = "ref.pkl"
if os.path.exists(filename):
    with open(filename, 'rb') as f:
        ref = pickle.load(f)

In [ ]:
def value_iteration(states,actions,rewards,trans,ref):
  # Initialize the value function and policy
  V = utility()
  Pi = {}
  # policy = {state: {action: 0 for action in environment.actions(state)} for state in environment.states}
  i = 0
  # Repeat until convergence
  while True:
    i+=1
    print(i)
    # Initialize an empty update
    updated = False

    # Iterate over all states
    for state in states.keys():
      if state[1] == state[0]:
        continue
      elif state[0] == state[2]:
        continue
      elif state[1] in graph[state[0]]:
        Pi[state] = state[1]
        continue
      elif state[2] in graph[state[0]]:
        Pi[state] =random.choice([y for y in [x for x in graph[state[0]]] if y != state[2]]) #not in graph[state[2]]])
        continue
      # Initialize the minimum value and the best action
      min_value = float('inf')
      best_action = None

      # Iterate over all actions
      for action in actions[state]:
        # Compute the expected value of the action
        expected_value = 0
        for x in ref[state]:
          if x[0] == action:
            expected_value += trans[(state,x)] * (rewards[(state,action)] + V[x])

        # Update the minimum value and the best action
        if expected_value < min_value:
          min_value = expected_value
          best_action = action

      # Update the value function and policy
      if abs(V[state] - min_value) > 0.0001:
        updated = True
        V[state] = min_value
        Pi[state] = best_action
        
    # Return the value function and policy if convergence has been reached
  
    if not updated:
      return (V, Pi)

In [ ]:
V,Pi = value_iteration(states,actions,rewards,trans,ref)

In [ ]:
# import pickle
# import os

# filename = "opAction.pkl"
# with open(filename, 'wb') as f:
#     pickle.dump(Pi,f)

In [65]:
import pickle
filename = "Utility.pkl"
if os.path.exists(filename):
    with open(filename, 'rb') as f:
        V = pickle.load(f)

In [66]:
import pickle
filename = "opAction.pkl"
if os.path.exists(filename):
    with open(filename, 'rb') as f:
        Pi = pickle.load(f)

In [ ]:
print(V)

Visualization

In [ ]:
import networkx as nx
import matplotlib.pyplot as plt
G = nx.Graph()
G.add_nodes_from([x for x in range(1,51)])
for key,value in graph.items():
    for i in value:
        G.add_edge(key, i)      

def displayState(currentState): 

    #assigning colours to nodes
    color_map = []
    for node in G:
        if node == currentState[0]:
            color_map.append('blue')
        elif node == currentState[1]: 
            color_map.append('green')
        elif node == currentState[2]:
            color_map.append('red')
        else:
            color_map.append('cyan')

    nx.draw(G, with_labels = True, node_color = color_map)
    plt.show()

AGENT U-STAR

In [41]:
import random

Positions = {"Agent": None,"Prey":None,"Pred":None}

def spawn(graph,Positions):
    Agent_pos = random.choice(list(graph.keys()))
    Positions["Agent"] = Agent_pos
    Positions["Prey"] = random.choice([x for x in list(graph.keys()) if x != Agent_pos])
    Positions["Pred"] = random.choice([x for x in list(graph.keys()) if x!= Agent_pos and x not in graph[Agent_pos]])

    return Positions
    

In [64]:
def agent_util(Positions):
    steps = 0    
    currentState = (Positions["Agent"], Positions["Prey"], Positions["Pred"])
    for i in range(100):
        agent_pos = Pi[currentState]
        steps +=1
        if agent_pos == currentState[1]:
                print(steps)     
                return "Success"
        elif agent_pos == currentState[2]:
                return "Faliure"
        prey_pos = move_prey(currentState[1])
        pred_pos = move_distracted_predator(currentState[2],agent_pos, False)
        currentState = (agent_pos,prey_pos,pred_pos)
        print(currentState)
        # displayState(currentState)
        if agent_pos == currentState[1]:
                print(steps)
                return "Success"
        elif agent_pos == currentState[2]:
                print("Fail", currentState)
                return "Faliure"
        
        
    return "Faliure 2"

In [67]:
def success():
    count = 0
    count2 = 0
    for i in range(1000):
        Positions = {"Agent": None,"Prey":None,"Pred":None}
        Positions = spawn(graph,Positions)
        result = agent_util(Positions)
        if result == "Success":
            count +=1
        elif result == "Faliure":
            count2 +=1
    print("Success rate: ",count/10, "%")
    print("Faliure rate: ", count2/10, "%")

success()

(11, 6, 29)
(10, 7, 30)
(6, 8, 29)
(7, 3, 28)
(8, 2, 27)
(3, 1, 28)
(2, 50, 29)
(1, 49, 30)
9
(41, 30, 46)
(37, 31, 45)
(38, 32, 42)
(33, 31, 43)
(32, 32, 40)
5
(10, 13, 41)
(11, 14, 42)
(12, 13, 41)
4
(6, 31, 45)
(10, 31, 44)
(11, 32, 45)
(16, 33, 46)
(17, 33, 45)
(18, 32, 44)
(19, 33, 43)
(20, 33, 40)
(21, 32, 41)
(22, 33, 40)
(27, 33, 41)
(28, 38, 37)
(29, 38, 38)
(30, 39, 39)
(31, 35, 40)
(32, 35, 41)
(33, 35, 40)
(32, 36, 41)
(33, 37, 40)
(32, 41, 39)
(31, 37, 40)
(32, 38, 39)
(31, 37, 38)
(30, 41, 33)
(29, 40, 32)
(28, 43, 31)
(27, 44, 32)
(22, 44, 33)
(23, 43, 32)
(21, 44, 33)
(20, 45, 32)
(19, 46, 33)
(18, 46, 32)
(17, 46, 33)
(16, 47, 32)
(11, 48, 33)
(12, 49, 34)
(7, 1, 33)
(8, 2, 32)
(3, 3, 33)
40
1
(28, 5, 33)
(27, 4, 34)
(22, 5, 33)
(21, 5, 38)
(20, 4, 33)
(19, 3, 32)
(18, 8, 33)
(17, 7, 34)
(16, 6, 35)
(11, 6, 39)
(10, 10, 38)
11
(3, 38, 10)
(2, 38, 11)
(48, 38, 12)
(47, 39, 13)
(46, 35, 12)
(45, 35, 7)
(42, 39, 8)
(41, 39, 9)
(40, 39, 8)
10
(37, 31, 35)
(41, 32, 34)
(42,

In [ ]:
# displayState(currentState=(1,2,3))

In [ ]:
import networkx as nx
G = nx.Graph()

G.add_nodes_from([x for x in range(1,51)])
for key,value in graph.items():
    for i in value:
        G.add_edge(key, i)

def displayState(currentState):        
    #assigning colours to nodes
    color_map = []
    for node in G:
        if node == 2:
            color_map.append('blue')
        elif node == 5: 
            color_map.append('green')
        elif node == 8:
            color_map.append('red')
        else:
            color_map.append('cyan')

    nx.draw(G, with_labels = True, node_color = color_map)

In [ ]:
X = []
for state in states.keys():
    X.append([state[0],state[1],state[2]])
X = np.array(X)
print(X)

In [ ]:
y = np.array(V_list)
y = np.insert(y, 0, 1)
print(y[16482])

U Partial

In [43]:

def prey_prob_initial(graph,agent_pos):
    prob_dic = {}
    for nodes in graph:
        if nodes == agent_pos:
            prob_dic[nodes] = 0
        else:
            prob_dic[nodes] = 1/49
    return list(prob_dic.values()),prob_dic

def prey_prob_updates_Agent(prob_dic,prey_found,surveyed_node):
    prob_dic_update = {}
    for nodes in prob_dic:
        if prey_found == False: #* Case 1
            if nodes != surveyed_node:
                prob_dic_update[nodes] = prob_dic[nodes] / (1 - prob_dic[surveyed_node])
            else:
                prob_dic_update[nodes] = 0
        elif prey_found == True: #* Case 2
            if nodes != surveyed_node:
                prob_dic_update[nodes] = 0
            else:
                prob_dic_update[nodes] = 1
    
    #prob_dic = prob_dic_update
    return list(prob_dic_update.values()),prob_dic_update

def prey_prob_updates_prey(prob_dic,graph): #* When prey moves, ie. t+1
    prob_dic_update = {}
    for nodes in prob_dic:
        prob_update = 0
        for sub_nodes in prob_dic:
            if sub_nodes == nodes:
                prob_update +=  prob_dic[sub_nodes] * (1/(len(graph[sub_nodes])+1)) # was 0
            else:
                if nodes in graph[sub_nodes]:
                    prob_update += prob_dic[sub_nodes] * (1/(len(graph[sub_nodes])+1))
                else:
                    prob_update += 0
        prob_dic_update[nodes] = prob_update
    
    return list(prob_dic_update.values()), prob_dic_update

In [44]:
Vpartial = {}
for agent in range(1,51):
    for pred in range(1,51):
        Vpartial[(agent,pred)] = 0



In [45]:
ref_Partial = {}

for row in Vpartial:
    for col in Vpartial:
        if col[0] in graph[row[0]]:
            if col[1] in graph[row[1]]:
                if row in ref_Partial.keys():
                    ref_Partial[row].append(col)
                else:
                    ref_Partial[row] = [col]

In [ ]:
print(ref_Partial)

In [46]:
for state in ref_Partial.keys():
    for action in [x for x in graph[state[0]]]:
        print(state, action)

(1, 1) 49
(1, 1) 2
(1, 1) 50
(1, 2) 49
(1, 2) 2
(1, 2) 50
(1, 3) 49
(1, 3) 2
(1, 3) 50
(1, 4) 49
(1, 4) 2
(1, 4) 50
(1, 5) 49
(1, 5) 2
(1, 5) 50
(1, 6) 49
(1, 6) 2
(1, 6) 50
(1, 7) 49
(1, 7) 2
(1, 7) 50
(1, 8) 49
(1, 8) 2
(1, 8) 50
(1, 9) 49
(1, 9) 2
(1, 9) 50
(1, 10) 49
(1, 10) 2
(1, 10) 50
(1, 11) 49
(1, 11) 2
(1, 11) 50
(1, 12) 49
(1, 12) 2
(1, 12) 50
(1, 13) 49
(1, 13) 2
(1, 13) 50
(1, 14) 49
(1, 14) 2
(1, 14) 50
(1, 15) 49
(1, 15) 2
(1, 15) 50
(1, 16) 49
(1, 16) 2
(1, 16) 50
(1, 17) 49
(1, 17) 2
(1, 17) 50
(1, 18) 49
(1, 18) 2
(1, 18) 50
(1, 19) 49
(1, 19) 2
(1, 19) 50
(1, 20) 49
(1, 20) 2
(1, 20) 50
(1, 21) 49
(1, 21) 2
(1, 21) 50
(1, 22) 49
(1, 22) 2
(1, 22) 50
(1, 23) 49
(1, 23) 2
(1, 23) 50
(1, 24) 49
(1, 24) 2
(1, 24) 50
(1, 25) 49
(1, 25) 2
(1, 25) 50
(1, 26) 49
(1, 26) 2
(1, 26) 50
(1, 27) 49
(1, 27) 2
(1, 27) 50
(1, 28) 49
(1, 28) 2
(1, 28) 50
(1, 29) 49
(1, 29) 2
(1, 29) 50
(1, 30) 49
(1, 30) 2
(1, 30) 50
(1, 31) 49
(1, 31) 2
(1, 31) 50
(1, 32) 49
(1, 32) 2
(1, 32) 50
(1,

In [47]:
# UstarList = {}
# for state in Vpartial.keys():
#             UstarList[state] =  [ val for key,val in V.items() if key[0] == state[0] and key[2] == state[1]]

In [53]:
import pickle
filename = "Utility.pkl"
if os.path.exists(filename):
    with open(filename, 'rb') as f:
        V = pickle.load(f)

In [54]:
def node_survey(node, prey_pos):
    if node == prey_pos:
        return(True)
    else:
        return(False)

def agent_Upartial(Positions):
    steps = 0    
    currentState = (Positions["Agent"], Positions["Prey"], Positions["Pred"])
    p,prob_dic = prey_prob_initial(graph,currentState[0])
    
    for i in range(1000):
        print(i, " : ",currentState)


        survey_node = random.choice([key for key, value in prob_dic.items() if value == max(prob_dic.values())])
        result = node_survey(survey_node,currentState[1])

        p, prob_dic = prey_prob_updates_Agent(prob_dic, result ,survey_node)#belief update at time t
 
        min_value = float('inf')
        
        best_action = None
        for agent in graph[currentState[0]]:
                expected_value = 0
                for prey in range(1,51):
                        expected_value += prob_dic[prey]*V[(agent, prey, currentState[2])]
                if expected_value < min_value:
                        min_value = expected_value
                        best_action = agent              

        agent_pos = best_action
        

        steps +=1
        if agent_pos == currentState[1]:
                     
                return "Success"
        elif agent_pos == currentState[2]:
                return "Faliure"
        
        p,prob_dic = prey_prob_updates_Agent(prob_dic,agent_pos == currentState[1],agent_pos) # updating beliefs at t
        
        prey_pos = move_prey(currentState[1])
        
        p,prob_dic = prey_prob_updates_prey(prob_dic,graph) #updating beliefs at t+1
        pred_pos = move_distracted_predator(currentState[2],agent_pos, False)
        currentState = (agent_pos,prey_pos,pred_pos)
        # print(currentState)
        # displayState(currentState)
        if agent_pos == currentState[1]:
                return "Success"
        elif agent_pos == currentState[2]:
                print("Fail", currentState)
                return "Faliure"
        
        
    return "Faliure 2"

In [55]:
def success():
    count = 0
    count2 = 0
    for i in range(1000):    
        Positions = {"Agent": None,"Prey":None,"Pred":None}#added this for steps
        Positions = spawn(graph,Positions)
        result = agent_Upartial(Positions)
        if result == "Success":
            count +=1
        elif result == "Faliure":
            count2 +=1
    print("Success rate: ",count/10, "%")
    print("Faliure rate: ", count2/10, "%")

success()

0  :  (40, 25, 47)
1  :  (41, 25, 46)
2  :  (37, 25, 47)
3  :  (38, 25, 48)
4  :  (33, 26, 2)
5  :  (32, 25, 3)
6  :  (33, 26, 8)
7  :  (38, 25, 7)
8  :  (37, 26, 8)
9  :  (41, 26, 9)
10  :  (42, 27, 8)
11  :  (45, 27, 3)
12  :  (42, 22, 8)
13  :  (41, 21, 7)
14  :  (37, 23, 8)
15  :  (38, 23, 3)
16  :  (33, 21, 8)
17  :  (32, 23, 9)
18  :  (31, 23, 10)
19  :  (30, 22, 9)
20  :  (29, 22, 8)
21  :  (28, 27, 9)
0  :  (13, 41, 7)
1  :  (14, 41, 8)
2  :  (15, 37, 9)
3  :  (16, 41, 10)
4  :  (17, 41, 9)
5  :  (18, 42, 10)
6  :  (19, 43, 9)
7  :  (20, 43, 10)
8  :  (21, 42, 11)
9  :  (22, 43, 16)
10  :  (27, 40, 17)
11  :  (28, 40, 16)
12  :  (29, 41, 17)
13  :  (30, 40, 16)
14  :  (31, 40, 17)
15  :  (32, 41, 18)
16  :  (33, 42, 19)
17  :  (38, 41, 20)
18  :  (39, 37, 19)
19  :  (40, 38, 18)
20  :  (41, 37, 19)
21  :  (42, 37, 18)
22  :  (45, 37, 17)
23  :  (46, 37, 16)
24  :  (47, 38, 15)
25  :  (48, 39, 14)
26  :  (47, 39, 13)
27  :  (48, 38, 14)
28  :  (47, 39, 13)
29  :  (48, 40, 12)
30

V Model

In [ ]:
import numpy as np
# input for our model
X = []
for state in states.keys():
    X.append([state[0]/50,state[1]/50,state[2]/50])
inputs = np.array(X)
# print(X.shape)

# # Define the output data
outputs = np.array(list([v] for v in V.values()))
#outputs = np.transpose(outputs)
print(inputs)

In [ ]:
import numpy as np

def leaky_relu(x):
    return np.maximum(x, 0.01 * x)

# def tanh(x):
#     return np.tanh(x)

# def tanh_derivative(x):
#     return 1 - np.square(tanh(x))

def leaky_relu_derivative(x):
    x[x > 0] = 1
    x[x <= 0] = 0.01
    return x

def cross_entropy(predicted, true):
    # This function computes the cross-entropy loss between the predicted and true outputs
    loss = -(true * np.log(predicted) + (1 - true) * np.log(1 - predicted))
    return loss

def derivative(predicted, true):
    # This function computes the derivative of the cross-entropy loss with respect to the predicted output
    derivative = -(true / predicted) + (1 - true) / (1 - predicted)
    return derivative

nodes1 = 35
nodes2 = 35
def neural_network(inputs, targets, epochs, lr):
    print(inputs.shape)
    
    # Initialize weights and biases randomly
    W_layer1 = np.random.normal(0,0.1,(3, nodes1))
    # b1 = np.random.rand(nodes1)
    b_layer1 = np.zeros(nodes1)
    W_layer2 = np.random.normal(0,0.1,(nodes1,nodes2))
    b_layer2 = np.zeros(nodes2)
    W_layer3 = np.random.normal(0,0.1,(nodes2, 1))
    b_layer3 = np.zeros(1)
    
    for epoch in range(epochs):
        print("iter: ",epoch)
        # Forward propagation
 
        
        # # Calculate error
        # error = (np.array(output) - np.array(targets))**2
        
  
        
        # # Select a batch of data
        batch_size = 500
        batch_indices = np.random.choice(len(inputs), batch_size)
        #print(batch_indices)
        batch_inputs = inputs[batch_indices]
        #print(batch_inputs)
        batch_targets = targets[batch_indices]
        #print(batch_targets)

        # Forward propagation
        layer1 = leaky_relu(np.dot(batch_inputs, W_layer1) + b_layer1)
        layer2 = leaky_relu(np.dot(layer1, W_layer2) + b_layer2)
        output = np.dot(layer2, W_layer3) + b_layer3

        # Calculate error
        #error = (np.array(output) - np.array(batch_targets))**2
        error = cross_entropy(output, batch_targets)
        

        # Backpropagation
        #derivative3 = np.ones(error.shape)
        derivative3 = derivative(output, batch_targets)
        derivative2 = derivative3.dot(W_layer3.T) * leaky_relu_derivative(layer2)
        derivative1 = derivative2.dot(W_layer2.T) * leaky_relu_derivative(layer1)

        W_layer3 += lr * layer2.T.dot(derivative3) / len(inputs)
        b_layer3 += lr * np.sum(derivative3) / len(inputs)

        W_layer2 += lr * layer1.T.dot(derivative2) / len(inputs)
        b_layer2 += lr * np.sum(derivative2) / len(inputs)

        W_layer1 += lr * batch_inputs.T.dot(derivative1) / len(inputs)
        b_layer1 += lr * np.sum(derivative1) / len(inputs)

    # return np.round(output.squeeze())
    return output

    # Training the network for 1000 epochs with a learning rate of  0.01
outputs = neural_network(inputs, outputs, 1000, 0.01)
print(outputs.shape)

In [ ]:
 #------------------- DUMPING UTILITY FILE SO THAT IT WILL BE DIRECTLY CALLED LATER TO RUN THE AGENT----------------------------------
# import pickle
# import os

# filename = "VmodelU.pkl"
# with open(filename, 'wb') as f:
#     pickle.dump(V,f)

In [35]:
 #------------------- LOAD UTILITY FILE SO THAT IT WILL BE DIRECTLY CALLED HERE TO RUN THE AGENT----------------------------------
import pickle
filename = "VmodelU.pkl"
if os.path.exists(filename):
    with open(filename, 'rb') as f:
        output = pickle.load(f)

Agent V Model 

In [59]:
import pickle
filename = "Utility.pkl"
if os.path.exists(filename):
    with open(filename, 'rb') as f:
        V = pickle.load(f)

In [36]:
index = 0
for agent in range(1,51):
    for prey in range(1,51):
        for pred in range(1,51):
            V[(agent, prey,pred)] = output[index]
            index+=1

In [37]:
def agent_V_Model(Positions):
    steps = 0    
    currentState = (Positions["Agent"], Positions["Prey"], Positions["Pred"])
    
    for i in range(1000):
        print(i, " : ",currentState)

        min_value = float('inf')
        best_action = None

        # Iterate over all actions
        for action in [x for x in graph[currentState[0]]]:
                # Compute the expected value of the action
                expected_value = 0
                for x in ref[currentState]:
                        if x[0] == action:
                                expected_value += V[x]

                if expected_value < min_value:
                        min_value = expected_value
                        best_action = action
                
        agent_pos = best_action
        steps +=1
        if agent_pos == currentState[1]:
                print(steps)     
                return "Success"
        elif agent_pos == currentState[2]:
                return "Faliure"
        
        prey_pos = move_prey(currentState[1])
        
        pred_pos = move_distracted_predator(currentState[2],agent_pos, False)
        currentState = (agent_pos,prey_pos,pred_pos)
        # print(currentState)
        # displayState(currentState)
        if agent_pos == currentState[1]:
                print(steps)
                return "Success"
        elif agent_pos == currentState[2]:
                print("Fail", currentState)
                return "Faliure"
        
        
    return "Faliure 2"

In [42]:
def success():
    count = 0
    count2 = 0
    for i in range(1000):
        Positions = {"Agent": None,"Prey":None,"Pred":None}
        Positions = spawn(graph,Positions)
        result = agent_V_Model(Positions)
        if result == "Success":
            count +=1
        elif result == "Faliure":
            count2 +=1
    print("Success rate: ",count/10, "%")
    print("Faliure rate: ", count2/10, "%")

success()

0  :  (40, 20, 32)
1  :  (43, 21, 31)
2  :  (44, 20, 32)
3  :  (45, 21, 33)
4  :  (46, 22, 34)
5  :  (47, 23, 36)
6  :  (48, 22, 35)
7  :  (49, 22, 39)
8  :  (50, 27, 40)
9  :  (49, 22, 41)
10  :  (50, 21, 40)
11  :  (49, 22, 41)
12  :  (50, 23, 40)
13  :  (49, 21, 41)
14  :  (50, 21, 40)
15  :  (49, 23, 43)
16  :  (50, 21, 40)
17  :  (49, 22, 39)
18  :  (50, 27, 40)
19  :  (49, 28, 41)
20  :  (50, 28, 40)
21  :  (49, 29, 39)
22  :  (50, 30, 40)
23  :  (49, 29, 41)
24  :  (50, 30, 42)
25  :  (49, 30, 43)
26  :  (50, 31, 42)
27  :  (49, 32, 41)
28  :  (50, 32, 40)
29  :  (49, 33, 41)
30  :  (50, 38, 42)
31  :  (49, 33, 41)
32  :  (50, 32, 40)
33  :  (49, 33, 41)
34  :  (50, 34, 37)
35  :  (49, 34, 41)
36  :  (50, 35, 37)
37  :  (49, 35, 41)
38  :  (50, 35, 37)
39  :  (49, 35, 38)
40  :  (50, 36, 37)
41  :  (49, 36, 38)
42  :  (50, 34, 33)
43  :  (49, 36, 34)
44  :  (48, 35, 36)
45  :  (49, 36, 35)
46  :  (50, 37, 34)
47  :  (49, 37, 33)
48  :  (50, 41, 38)
49  :  (49, 42, 37)
50  :  (50

V Partial

In [ ]:
V_partial_input = []

for state in states.keys():
    print("curr state: ", state)
    x = [bfs(state[0],state[2])]
    for nodes in range(1,51):
        x.append(bfs(state[0],nodes))
    V_partial_input.append(x)

In [ ]:
import numpy as np

def leaky_relu(x):
    return np.maximum(x, 0.01 * x)

# def tanh(x):
#     return np.tanh(x)

# def tanh_derivative(x):
#     return 1 - np.square(tanh(x))

def leaky_relu_derivative(x):
    x[x > 0] = 1
    x[x <= 0] = 0.01
    return x

def cross_entropy(predicted, true):
    # This function computes the cross-entropy loss between the predicted and true outputs
    loss = -(true * np.log(predicted) + (1 - true) * np.log(1 - predicted))
    return loss

def derivative(predicted, true):
    # This function computes the derivative of the cross-entropy loss with respect to the predicted output
    derivative = -(true / predicted) + (1 - true) / (1 - predicted)
    return derivative

nodes1 = 35
nodes2 = 35
def neural_network(inputs, targets, epochs, lr):
    print(inputs.shape)
    
    # Initialize weights and biases randomly
    W_layer1 = np.random.normal(0,0.1,(3, nodes1))
    # b1 = np.random.rand(nodes1)
    b_layer1 = np.zeros(nodes1)
    W_layer2 = np.random.normal(0,0.1,(nodes1,nodes2))
    b_layer2 = np.zeros(nodes2)
    W_layer3 = np.random.normal(0,0.1,(nodes2, 1))
    b_layer3 = np.zeros(1)
    
    for epoch in range(epochs):
        print("iter: ",epoch)
        # Forward propagation
 
        
        # # Calculate error
        # error = (np.array(output) - np.array(targets))**2
        
  
        
        # # Select a batch of data
        batch_size = 500
        batch_indices = np.random.choice(len(inputs), batch_size)
        #print(batch_indices)
        batch_inputs = inputs[batch_indices]
        #print(batch_inputs)
        batch_targets = targets[batch_indices]
        #print(batch_targets)

        # Forward propagation
        layer1 = leaky_relu(np.dot(batch_inputs, W_layer1) + b_layer1)
        layer2 = leaky_relu(np.dot(layer1, W_layer2) + b_layer2)
        output = np.dot(layer2, W_layer3) + b_layer3

        # Calculate error
        #error = (np.array(output) - np.array(batch_targets))**2
        error = cross_entropy(output, batch_targets)
        

        # Backpropagation
        #derivative3 = np.ones(error.shape)
        derivative3 = derivative(output, batch_targets)
        derivative2 = derivative3.dot(W_layer3.T) * leaky_relu_derivative(layer2)
        derivative1 = derivative2.dot(W_layer2.T) * leaky_relu_derivative(layer1)

        W_layer3 += lr * layer2.T.dot(derivative3) / len(inputs)
        b_layer3 += lr * np.sum(derivative3) / len(inputs)

        W_layer2 += lr * layer1.T.dot(derivative2) / len(inputs)
        b_layer2 += lr * np.sum(derivative2) / len(inputs)

        W_layer1 += lr * batch_inputs.T.dot(derivative1) / len(inputs)
        b_layer1 += lr * np.sum(derivative1) / len(inputs)

    # return np.round(output.squeeze())
    return output

    # Training the network for 1000 epochs with a learning rate of  0.01
outputs = neural_network(inputs, outputs, 1000, 0.01)
print(outputs.shape)

In [ ]:
# import pickle
# import os

# filename = "V_partial_input.pkl"
# with open(filename, 'wb') as f:
#     pickle.dump(V_partial_input,f)

In [ ]:
# import pickle
# import os
# filename = "V_partial_input.pkl"
# if os.path.exists(filename):
#     with open(filename, 'rb') as f:
#         V_partial_input = pickle.load(f)

In [60]:
import pickle
import os
filename = "VmodelU.pkl"
if os.path.exists(filename):
    with open(filename, 'rb') as f:
        output= pickle.load(f)

In [61]:
index = 0
for agent in range(1,51):
    for prey in range(1,51):
        for pred in range(1,51):
            V[(agent, prey,pred)] = output[index]
            index+=1

In [62]:
def node_survey(node, prey_pos):
    if node == prey_pos:
        return(True)
    else:
        return(False)

def agent_Vpartial(Positions):
    steps = 0    
    currentState = (Positions["Agent"], Positions["Prey"], Positions["Pred"])
    p,prob_dic = prey_prob_initial(graph,currentState[0])
    
    for i in range(1000):
        print(i, " : ",currentState)


        survey_node = random.choice([key for key, value in prob_dic.items() if value == max(prob_dic.values())])
        result = node_survey(survey_node,currentState[1])

        p, prob_dic = prey_prob_updates_Agent(prob_dic, result ,survey_node)#belief update at time t
 
        min_value = float('inf')
        
        best_action = None
        for agent in graph[currentState[0]]:
                expected_value = 0
                for prey in range(1,51):
                        expected_value += prob_dic[prey]*V[(agent, prey, currentState[2])]
                if expected_value < min_value:
                        min_value = expected_value
                        best_action = agent              

        agent_pos = best_action
        

        steps +=1
        if agent_pos == currentState[1]:
                     
                return "Success"
        elif agent_pos == currentState[2]:
                return "Faliure"
        
        p,prob_dic = prey_prob_updates_Agent(prob_dic,agent_pos == currentState[1],agent_pos) # updating beliefs at t
        
        prey_pos = move_prey(currentState[1])
        
        p,prob_dic = prey_prob_updates_prey(prob_dic,graph) #updating beliefs at t+1
        pred_pos = move_distracted_predator(currentState[2],agent_pos, False)
        currentState = (agent_pos,prey_pos,pred_pos)
        # print(currentState)
        # displayState(currentState)
        if agent_pos == currentState[1]:
                return "Success"
        elif agent_pos == currentState[2]:
                print("Fail", currentState)
                return "Faliure"
        
        
    return "Faliure 2"

In [63]:
def success():
    count = 0
    count2 = 0
    for i in range(1000):
        Positions = {"Agent": None,"Prey":None,"Pred":None}
        Positions = spawn(graph,Positions)
        result = agent_Vpartial(Positions)
        if result == "Success":
            count +=1
        elif result == "Faliure":
            count2 +=1
    print("Success rate: ",count/10, "%")
    print("Faliure rate: ", count2/10, "%")

success()

0  :  (1, 48, 35)
1  :  (49, 47, 34)
2  :  (48, 47, 33)
0  :  (37, 30, 20)
1  :  (36, 29, 19)
2  :  (34, 29, 18)
3  :  (33, 29, 17)
4  :  (32, 29, 18)
5  :  (31, 30, 19)
0  :  (18, 48, 31)
1  :  (17, 47, 32)
2  :  (16, 48, 31)
3  :  (15, 2, 32)
4  :  (14, 1, 31)
5  :  (15, 49, 30)
6  :  (14, 48, 29)
7  :  (15, 47, 30)
8  :  (14, 47, 29)
9  :  (15, 48, 30)
10  :  (14, 2, 29)
11  :  (15, 48, 28)
12  :  (14, 49, 27)
13  :  (13, 50, 26)
14  :  (12, 1, 27)
15  :  (11, 49, 22)
16  :  (12, 49, 21)
17  :  (13, 50, 20)
18  :  (12, 49, 19)
19  :  (7, 49, 18)
20  :  (6, 1, 17)
21  :  (5, 1, 16)
22  :  (4, 1, 11)
23  :  (3, 1, 12)
24  :  (2, 1, 13)
0  :  (25, 1, 4)
1  :  (26, 1, 3)
2  :  (27, 49, 4)
3  :  (28, 49, 3)
4  :  (29, 48, 8)
5  :  (28, 2, 9)
6  :  (27, 3, 10)
7  :  (26, 3, 9)
8  :  (27, 3, 10)
9  :  (26, 4, 11)
10  :  (25, 4, 16)
11  :  (26, 5, 17)
12  :  (27, 4, 18)
13  :  (28, 4, 19)
14  :  (29, 4, 20)
15  :  (30, 4, 21)
16  :  (31, 4, 22)
17  :  (32, 3, 21)
18  :  (33, 4, 23)
19  :  (